<a href="https://colab.research.google.com/github/mevivekmevivek/Drug-Efficacy-Prediction/blob/main/CCLE_model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt 
import seaborn as sns

from sklearn.linear_model import ElasticNet, Lasso,  BayesianRidge, LassoLarsIC
from sklearn.ensemble import RandomForestRegressor,  GradientBoostingRegressor
from sklearn.kernel_ridge import KernelRidge
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import RobustScaler,StandardScaler,OneHotEncoder
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import KFold, cross_val_score, train_test_split
from sklearn.metrics import mean_squared_error,auc

import warnings
warnings.filterwarnings('ignore')

In [ ]:
import zipfile
!unzip /content/CCLE_Integrateddata.zip

full_data = pd.read_csv('/content/CCLE_Integrateddata.zip')

Archive:  /content/CCLE_Integrateddata.zip
  inflating: CCLE_Integrateddata.csv  


In [ ]:
full_data

Unnamed: 0  Unnamed: 0.1  ... rna_feature_98 rna_feature_99
0               0             1  ...       0.340322       0.137018
1               1           504  ...       0.340322       0.137018
2               2          1007  ...       0.340322       0.137018
3               3          1511  ...       0.340322       0.137018
4               4          2014  ...       0.340322       0.137018
...           ...           ...  ...            ...            ...
10848       10848          9272  ...       0.541737      -0.047450
10849       10849          9776  ...       0.541737      -0.047450
10850       10850         10280  ...       0.541737      -0.047450
10851       10851         10784  ...       0.541737      -0.047450
10852       10852         11286  ...       0.541737      -0.047450

[10853 rows x 156 columns]

In [ ]:
full_data['labels']

0       -1.109567
1        0.845836
2        2.079442
3        2.079442
4        2.079442
           ...   
10848    2.079442
10849    1.828960
10850    2.079442
10851    1.094251
10852    2.079442
Name: labels, Length: 10853, dtype: float64

In [ ]:
y = full_data['labels']
#

In [ ]:
full_data.drop(columns =['labels'], inplace = True)
train_data, test_data, train_ic50, test_ic50 = train_test_split( full_data, y, test_size=1/10, random_state=0)

In [ ]:
train_data.drop(columns=['drug_id', 'cell_line_id', 'Unnamed: 0','Unnamed: 0.1', 'Name'], inplace= True)
test_data.drop(columns=['drug_id', 'cell_line_id', 'Unnamed: 0', 'Unnamed: 0.1','Name'], inplace= True)

In [ ]:
full_data.drop(columns=['drug_id', 'cell_line_id', 'Unnamed: 0','Unnamed: 0.1', 'Name'], inplace= True)


In [ ]:
!pip install xgboost

In [ ]:
import xgboost
from xgboost import plot_importance
from collections import OrderedDict
lasso = Lasso(alpha =0.0005)
model = xgboost.XGBRegressor(tree_method='gpu_hist',colsample_bytree=0.4,
                 gamma=0,                 
                 learning_rate=0.07,
                 max_depth=9,
                 min_child_weight=1.5,
                 n_estimators=2000,                                                                    
                 reg_alpha=0.75,
                 reg_lambda=0.45,
                 subsample=0.6,
                 seed=42
                 ) 



In [ ]:
def mse(y, y_pred):
    return mean_squared_error(y, y_pred)

In [ ]:
from sklearn.model_selection import KFold, cross_val_score
from sklearn.model_selection import cross_validate

n_folds = 10 # number of folds
def get_cv_scores(model, X, y, print_scores=True):
    kf = KFold(n_folds, shuffle=True, random_state=42).get_n_splits(X) # create folds
    scores = cross_validate(model, X, y, cv=kf,
                         scoring=('r2', 'neg_mean_squared_error'),
                         return_train_score=True)
      
    #rmse = -cross_val_score(model, X, y, scoring="neg_mean_squared_error", cv = kf) # get rmse
    #r2 = cross_val_score(model, X, y, scoring="r2", cv = kf) # get rmse
    if print_scores:
      print(scores['test_neg_mean_squared_error'], "Mean MSE :",scores['test_neg_mean_squared_error'].mean())
      print(scores['test_r2'], "Mean R2 :",scores['test_r2'].mean())
    #     print(f'Root mean squared error: {rmse.mean():.3f} ({rmse.std():.3f})')
    #     print(f'R2: {r2.mean():.3f} ({r2.std():.3f})')
    return scores

In [ ]:
get_cv_scores(model,full_data,y)

[15:01:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:02:17] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:02:40] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:03:03] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:03:26] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:03:49] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:04:12] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[15:04:34] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of re

{'fit_time': array([23.06151223, 22.54418111, 22.1730597 , 22.20244551, 22.18164039,
        22.37782383, 22.11748099, 22.28179264, 22.27832627, 22.12769032]),
 'score_time': array([0.22151971, 0.21865487, 0.21819544, 0.21878433, 0.21800232,
        0.2183938 , 0.21864486, 0.21780801, 0.21841908, 0.21700835]),
 'test_neg_mean_squared_error': array([-1.53999387, -1.62132171, -1.53572666, -1.85682908, -1.48825842,
        -1.85516605, -1.78114259, -1.4773541 , -1.78444915, -1.57768561]),
 'test_r2': array([0.60169728, 0.57816775, 0.57318363, 0.51209275, 0.59955376,
        0.52767085, 0.55500278, 0.57901677, 0.54069061, 0.60847118]),
 'train_neg_mean_squared_error': array([-0.1697529 , -0.17562053, -0.17562193, -0.17309011, -0.17554388,
        -0.17147155, -0.17737235, -0.17396319, -0.1727867 , -0.17485999]),
 'train_r2': array([0.95550221, 0.95400453, 0.95432101, 0.95471555, 0.95419396,
        0.95497979, 0.95332872, 0.95486881, 0.95469154, 0.95395302])}

In [ ]:
! pip install lightgbm --no-deps  --upgrade --force-reinstall --install-option=--gpu

/usr/local/lib/python3.7/dist-packages/pip/_internal/commands/install.py:232: UserWarning: Disabling all use of wheels due to the use of --build-option / --global-option / --install-option.
  cmdoptions.check_install_build_global(options)
     |████████████████████████████████| 1.5 MB 5.0 MB/s 
Skipping wheel build for lightgbm, due to binaries being disabled for it.
  Attempting uninstall: lightgbm
    Found existing installation: lightgbm 2.2.3
    Uninstalling lightgbm-2.2.3:
      Successfully uninstalled lightgbm-2.2.3
    Running setup.py install for lightgbm ... done


In [ ]:
import lightgbm as lgb

model_lgb = lgb.LGBMRegressor(device_type="gpu",objective='regression',num_leaves=5,
                              learning_rate=0.05, n_estimators=18000,
                              max_bin = 55, bagging_fraction = 0.8,
                              bagging_freq = 5, feature_fraction = 0.2319,
                              feature_fraction_seed=9, bagging_seed=9,
                              min_data_in_leaf =6, min_sum_hessian_in_leaf = 11)


In [ ]:
 import re

# dfs = [train_data, train_ic50, test_data, test_ic50]
train_data = train_data.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))
test_data = test_data.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))


get_cv_scores(model_lgb,train_data, train_ic50)

[LightGBM] [Warning] feature_fraction is set=0.2319, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2319
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] feature_fraction is set=0.2319, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2319
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] 

{'fit_time': array([18.61325884, 12.62878919, 12.50998974, 12.55942702, 12.59350848,
        12.48984504, 12.52326941, 12.53037786, 12.63865232, 12.56209254]),
 'score_time': array([0.71787453, 0.73607492, 0.73601413, 0.74566245, 0.75433707,
        0.75038338, 0.74135613, 0.74081016, 0.75793457, 0.76454544]),
 'test_neg_mean_squared_error': array([-1.71202007, -1.46022311, -1.57112436, -1.44616731, -1.67338905,
        -1.52992021, -1.42529171, -1.53607867, -1.62091761, -1.33857974]),
 'test_r2': array([0.56791159, 0.64115697, 0.61173696, 0.60287131, 0.60002043,
        0.62052615, 0.60537853, 0.60500388, 0.52033241, 0.61975921]),
 'train_neg_mean_squared_error': array([-0.25299829, -0.27578245, -0.26855686, -0.26765196, -0.26569325,
        -0.26081219, -0.27871753, -0.2577614 , -0.26286891, -0.26944892]),
 'train_r2': array([0.93382458, 0.92764578, 0.92957492, 0.93064267, 0.93005387,
        0.93164857, 0.9278371 , 0.93272254, 0.93238232, 0.93038414])}

In [ ]:
get_cv_scores(model_lgb,full_data, y)

[LightGBM] [Warning] feature_fraction is set=0.2319, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2319
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] feature_fraction is set=0.2319, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2319
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] 

{'fit_time': array([12.35637736, 12.57932591, 12.40639114, 12.4162035 , 12.24534321,
        12.45437098, 12.48295331, 12.34767962, 12.10929823, 12.15223432]),
 'score_time': array([0.84123111, 0.86759734, 0.85083699, 0.84344459, 0.8502295 ,
        0.85388017, 0.85675764, 0.85328674, 0.86254454, 0.83802557]),
 'test_neg_mean_squared_error': array([-1.35568569, -1.27769356, -1.27023619, -1.40439961, -1.35151219,
        -1.68829318, -1.43091731, -1.32391195, -1.40181418, -1.25942427]),
 'test_r2': array([0.6493666 , 0.66757224, 0.64696999, 0.63097478, 0.63634812,
        0.57015703, 0.64250238, 0.62274127, 0.63917917, 0.687453  ]),
 'train_neg_mean_squared_error': array([-0.31812606, -0.32821936, -0.32774393, -0.32189839, -0.32741317,
        -0.32012393, -0.33053935, -0.32610586, -0.32269185, -0.32848878]),
 'train_r2': array([0.91660874, 0.91403851, 0.91475431, 0.91578381, 0.91456551,
        0.9159508 , 0.91302651, 0.91539851, 0.91538312, 0.91349698])}

In [ ]:
!pip install catboost

     |████████████████████████████████| 76.4 MB 40 kB/s 


In [ ]:
from catboost import CatBoostRegressor
model_cat = CatBoostRegressor(
    iterations=10000,
    learning_rate=0.05,
    task_type='GPU')
get_cv_scores(model_cat,full_data, y)

In [ ]:
class StackingAveragedModels(BaseEstimator, RegressorMixin, TransformerMixin):
    def __init__(self, base_models, meta_model, n_folds=5, use_features_in_secondary=False):
        self.base_models = base_models
        self.meta_model = meta_model
        self.n_folds = n_folds
        self.use_features_in_secondary = use_features_in_secondary
        
    def fit(self, X, y):
        """Fit all the models on the given dataset"""
        self.base_models_ = [list() for x in self.base_models]
        self.meta_model_ = clone(self.meta_model)
        kfold = KFold(n_splits=self.n_folds, shuffle=True, random_state=42)
        
        # Train cloned base models and create out-of-fold predictions
        out_of_fold_predictions = np.zeros((X.shape[0], len(self.base_models)))
        for i, model in enumerate(self.base_models):
            for train_index, holdout_index in kfold.split(X, y):
                instance = clone(model)
                self.base_models_[i].append(instance)
                instance.fit(X.iloc[train_index], y.iloc[train_index])
                y_pred = instance.predict(X.iloc[holdout_index])
                out_of_fold_predictions[holdout_index, i] = y_pred
        
        if self.use_features_in_secondary:
            self.meta_model_.fit(np.hstack((X, out_of_fold_predictions)), y)
        else:
            self.meta_model_.fit(out_of_fold_predictions, y)
            
        return self
    
    def predict(self, X):
        meta_features = np.column_stack([
            np.column_stack([model.predict(X) for model in base_models]).mean(axis=1)
            for base_models in self.base_models_ ])
        if self.use_features_in_secondary:
            return self.meta_model_.predict(np.hstack((X, meta_features)))
        else:
            return self.meta_model_.predict(meta_features)

In [ ]:
stacking_model1 = StackingAveragedModels([model, model_lgb, model_cat], lasso)
get_cv_scores(stacking_model1,full_data, y)

[16:01:16] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[16:01:33] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[16:01:51] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[16:02:09] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[16:02:27] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[LightGBM] [Warning] feature_fraction is set=0.2319, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2319
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6744853	total: 58.2s	remaining: 58.2s
5001:	learn: 0.6744808	total: 58.2s	remaining: 58.2s
5002:	learn: 0.6744789	total: 58.2s	remaining: 58.1s
5003:	learn: 0.6744789	total: 58.2s	remaining: 58.1s
5004:	learn: 0.6744787	total: 58.2s	remaining: 58.1s
5005:	learn: 0.6744786	total: 58.3s	remaining: 58.1s
5006:	learn: 0.6744786	total: 58.3s	remaining: 58.1s
5007:	learn: 0.6744782	total: 58.3s	remaining: 58.1s
5008:	learn: 0.6744782	total: 58.3s	remaining: 58.1s
5009:	learn: 0.6744182	total: 58.3s	remaining: 58.1s
5010:	learn: 0.6744182	total: 58.3s	remaining: 58.1s
5011:	learn: 0.6744013	total: 58.3s	remaining: 58s
5012:	learn: 0.6743568	total: 58.3s	remaining: 58s
5013:	learn: 0.6743545	total: 58.3s	remaining: 58s
5014:	learn: 0.6743541	total: 58.4s	remaining: 58s
5015:	learn: 0.6743506	total: 58.4s	remaining: 58s
5016:	learn: 0.6743504	total: 58.4s	remaining: 58s
5017:	learn: 0.6743229	total: 58.4s	remaining: 58s
5018:	lea

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6756015	total: 57.6s	remaining: 57.6s
5001:	learn: 0.6756014	total: 57.6s	remaining: 57.5s
5002:	learn: 0.6756008	total: 57.6s	remaining: 57.5s
5003:	learn: 0.6756005	total: 57.6s	remaining: 57.5s
5004:	learn: 0.6756004	total: 57.6s	remaining: 57.5s
5005:	learn: 0.6755701	total: 57.6s	remaining: 57.5s
5006:	learn: 0.6755701	total: 57.6s	remaining: 57.5s
5007:	learn: 0.6755701	total: 57.7s	remaining: 57.5s
5008:	learn: 0.6755692	total: 57.7s	remaining: 57.5s
5009:	learn: 0.6755601	total: 57.7s	remaining: 57.5s
5010:	learn: 0.6755601	total: 57.7s	remaining: 57.4s
5011:	learn: 0.6755599	total: 57.7s	remaining: 57.4s
5012:	learn: 0.6755162	total: 57.7s	remaining: 57.4s
5013:	learn: 0.6755017	total: 57.7s	remaining: 57.4s
5014:	learn: 0.6754823	total: 57.7s	remaining: 57.4s
5015:	learn: 0.6754820	total: 57.7s	remaining: 57.4s
5016:	learn: 0.6754665	total: 57.8s	remaining: 57.4s
5017:	learn: 0.6754354	total: 57.8s	remaining: 5

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6884322	total: 58.6s	remaining: 58.5s
5001:	learn: 0.6884321	total: 58.6s	remaining: 58.5s
5002:	learn: 0.6884321	total: 58.6s	remaining: 58.5s
5003:	learn: 0.6884321	total: 58.6s	remaining: 58.5s
5004:	learn: 0.6883401	total: 58.6s	remaining: 58.5s
5005:	learn: 0.6883401	total: 58.6s	remaining: 58.5s
5006:	learn: 0.6883400	total: 58.6s	remaining: 58.5s
5007:	learn: 0.6883250	total: 58.6s	remaining: 58.4s
5008:	learn: 0.6883250	total: 58.6s	remaining: 58.4s
5009:	learn: 0.6883237	total: 58.7s	remaining: 58.4s
5010:	learn: 0.6882097	total: 58.7s	remaining: 58.4s
5011:	learn: 0.6882046	total: 58.7s	remaining: 58.4s
5012:	learn: 0.6882046	total: 58.7s	remaining: 58.4s
5013:	learn: 0.6881686	total: 58.7s	remaining: 58.4s
5014:	learn: 0.6881333	total: 58.7s	remaining: 58.4s
5015:	learn: 0.6880905	total: 58.7s	remaining: 58.4s
5016:	learn: 0.6880904	total: 58.7s	remaining: 58.3s
5017:	learn: 0.6880904	total: 58.7s	remaining: 5

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6772463	total: 58.8s	remaining: 58.8s
5001:	learn: 0.6772463	total: 58.8s	remaining: 58.8s
5002:	learn: 0.6772331	total: 58.8s	remaining: 58.7s
5003:	learn: 0.6772263	total: 58.8s	remaining: 58.7s
5004:	learn: 0.6772010	total: 58.8s	remaining: 58.7s
5005:	learn: 0.6771999	total: 58.8s	remaining: 58.7s
5006:	learn: 0.6771459	total: 58.9s	remaining: 58.7s
5007:	learn: 0.6770119	total: 58.9s	remaining: 58.7s
5008:	learn: 0.6769913	total: 58.9s	remaining: 58.7s
5009:	learn: 0.6769913	total: 58.9s	remaining: 58.7s
5010:	learn: 0.6769912	total: 58.9s	remaining: 58.6s
5011:	learn: 0.6769904	total: 58.9s	remaining: 58.6s
5012:	learn: 0.6769896	total: 58.9s	remaining: 58.6s
5013:	learn: 0.6769877	total: 58.9s	remaining: 58.6s
5014:	learn: 0.6769421	total: 59s	remaining: 58.6s
5015:	learn: 0.6769421	total: 59s	remaining: 58.6s
5016:	learn: 0.6769421	total: 59s	remaining: 58.6s
5017:	learn: 0.6769421	total: 59s	remaining: 58.6s
501

...

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6531381	total: 1m 1s	remaining: 1m 1s
5001:	learn: 0.6531381	total: 1m 1s	remaining: 1m 1s
5002:	learn: 0.6531381	total: 1m 1s	remaining: 1m 1s
5003:	learn: 0.6530957	total: 1m 1s	remaining: 1m 1s
5004:	learn: 0.6530948	total: 1m 1s	remaining: 1m 1s
5005:	learn: 0.6530943	total: 1m 1s	remaining: 1m 1s
5006:	learn: 0.6530753	total: 1m 1s	remaining: 1m 1s
5007:	learn: 0.6530753	total: 1m 1s	remaining: 1m 1s
5008:	learn: 0.6530752	total: 1m 1s	remaining: 1m 1s
5009:	learn: 0.6530576	total: 1m 1s	remaining: 1m 1s
5010:	learn: 0.6530470	total: 1m 1s	remaining: 1m 1s
5011:	learn: 0.6528952	total: 1m 1s	remaining: 1m 1s
5012:	learn: 0.6528952	total: 1m 1s	remaining: 1m 1s
5013:	learn: 0.6528837	total: 1m 1s	remaining: 1m 1s
5014:	learn: 0.6528834	total: 1m 1s	remaining: 1m 1s
5015:	learn: 0.6528725	total: 1m 1s	remaining: 1m 1s
5016:	learn: 0.6528725	total: 1m 1s	remaining: 1m 1s
5017:	learn: 0.6528725	total: 1m 1s	remaining: 1

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6844276	total: 1m 2s	remaining: 1m 2s
5001:	learn: 0.6844270	total: 1m 2s	remaining: 1m 2s
5002:	learn: 0.6842661	total: 1m 2s	remaining: 1m 2s
5003:	learn: 0.6842661	total: 1m 2s	remaining: 1m 2s
5004:	learn: 0.6841262	total: 1m 2s	remaining: 1m 2s
5005:	learn: 0.6841262	total: 1m 2s	remaining: 1m 2s
5006:	learn: 0.6841229	total: 1m 2s	remaining: 1m 2s
5007:	learn: 0.6841115	total: 1m 2s	remaining: 1m 2s
5008:	learn: 0.6841083	total: 1m 2s	remaining: 1m 2s
5009:	learn: 0.6841077	total: 1m 2s	remaining: 1m 2s
5010:	learn: 0.6841061	total: 1m 2s	remaining: 1m 2s
5011:	learn: 0.6841045	total: 1m 2s	remaining: 1m 2s
5012:	learn: 0.6841022	total: 1m 2s	remaining: 1m 2s
5013:	learn: 0.6841016	total: 1m 2s	remaining: 1m 2s
5014:	learn: 0.6841005	total: 1m 2s	remaining: 1m 2s
5015:	learn: 0.6841003	total: 1m 2s	remaining: 1m 2s
5016:	learn: 0.6841003	total: 1m 2s	remaining: 1m 2s
5017:	learn: 0.6841003	total: 1m 2s	remaining: 1

Streaming output truncated to the last 5000 lines.
5000:	learn: 0.6786849	total: 1m	remaining: 1m
5001:	learn: 0.6786031	total: 1m	remaining: 1m
5002:	learn: 0.6786019	total: 1m	remaining: 1m
5003:	learn: 0.6786012	total: 1m	remaining: 1m
5004:	learn: 0.6786013	total: 1m	remaining: 1m
5005:	learn: 0.6786012	total: 1m	remaining: 1m
5006:	learn: 0.6786011	total: 1m	remaining: 1m
5007:	learn: 0.6786011	total: 1m	remaining: 1m
5008:	learn: 0.6785929	total: 1m	remaining: 1m
5009:	learn: 0.6784716	total: 1m	remaining: 1m
5010:	learn: 0.6783453	total: 1m	remaining: 1m
5011:	learn: 0.6783451	total: 1m	remaining: 1m
5012:	learn: 0.6783449	total: 1m	remaining: 1m
5013:	learn: 0.6783449	total: 1m	remaining: 1m
5014:	learn: 0.6783075	total: 1m	remaining: 1m
5015:	learn: 0.6783075	total: 1m	remaining: 1m
5016:	learn: 0.6783075	total: 1m	remaining: 1m
5017:	learn: 0.6783075	total: 1m	remaining: 1m
5018:	learn: 0.6782995	total: 1m	remaining: 1m
5019:	learn: 0.6782985	total: 1m	remaining: 1m
5020:	lea

Streaming output truncated to the last 5000 lines.
5002:	learn: 0.6524399	total: 1m 2s	remaining: 1m 2s
5003:	learn: 0.6524397	total: 1m 2s	remaining: 1m 2s
5004:	learn: 0.6524391	total: 1m 2s	remaining: 1m 2s
5005:	learn: 0.6524391	total: 1m 2s	remaining: 1m 2s
5006:	learn: 0.6524369	total: 1m 2s	remaining: 1m 2s
5007:	learn: 0.6524369	total: 1m 2s	remaining: 1m 2s
5008:	learn: 0.6524160	total: 1m 2s	remaining: 1m 2s
5009:	learn: 0.6524160	total: 1m 2s	remaining: 1m 2s
5010:	learn: 0.6524159	total: 1m 2s	remaining: 1m 2s
5011:	learn: 0.6524155	total: 1m 2s	remaining: 1m 2s
5012:	learn: 0.6524146	total: 1m 2s	remaining: 1m 2s
5013:	learn: 0.6524145	total: 1m 2s	remaining: 1m 2s
5014:	learn: 0.6524144	total: 1m 2s	remaining: 1m 2s
5015:	learn: 0.6524139	total: 1m 2s	remaining: 1m 2s
5016:	learn: 0.6524136	total: 1m 2s	remaining: 1m 2s
5017:	learn: 0.6524132	total: 1m 2s	remaining: 1m 2s
5018:	learn: 0.6524121	total: 1m 2s	remaining: 1m 2s
5019:	learn: 0.6524035	total: 1m 2s	remaining: 1

{'fit_time': array([755.4438417 , 761.96525002, 766.56408429, 776.93817639,
        779.72255087]),
 'score_time': array([8.28543997, 7.97928667, 8.35705805, 8.47437859, 8.46700001]),
 'test_neg_mean_squared_error': array([-1.21676152, -1.27425667, -1.29117915, -1.22129939, -1.1938344 ]),
 'test_r2': array([0.6970275 , 0.66875125, 0.6858036 , 0.67448273, 0.65390125]),
 'train_neg_mean_squared_error': array([-0.52807887, -0.53355597, -0.54596843, -0.58448629, -0.51799878]),
 'train_r2': array([0.86075008, 0.8608648 , 0.8551446 , 0.84852707, 0.86823163])}

In [ ]:
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
class AveragingModels(BaseEstimator, RegressorMixin, TransformerMixin):
    def __init__(self, models):
        self.models = models
  #      self.models_ = []
    # we define clones of the original models to fit the data in
    def fit(self, X, y):
        self.models_ = [clone(x) for x in self.models]
        # Train cloned base models
        for model in self.models_:
            model.fit(X, y)
        return self
    #Now we do the predictions for cloned models and average them
    def predict(self, X):
        predictions = np.column_stack([
            model.predict(X) for model in self.models_
        ])
        return np.mean(predictions, axis=1)

In [ ]:
averaged_models = AveragingModels(models = (model, model_lgb, model_cat))
get_cv_scores(averaged_models, train_data, train_ic50)